# Amazing Logos V4 - Step 4: Categories Consolidation Using Utils

This notebook consolidates categories using the consolidation utility:
- Loads metadata3.csv and analyzes categories directly
- Uses utils/consolidation.py to map categories to consolidated groups
- Creates analysis3.json with consolidated category analysis
- Replaces categories in metadata with consolidated ones
- Creates metadata4.csv with updated consolidated categories

In [1]:
import pandas as pd
import numpy as np
from pathlib import Path
import sys
from collections import defaultdict

# Add utils folder to path
utils_path = Path('../../utils')
sys.path.append(str(utils_path))

# Import consolidation functions
from consolidation2 import consolidate_categories, normalize_category, consolidation_map

# Paths
input_metadata_csv = Path('../../output/amazing_logos_v4/data/amazing_logos_v4_cleanup/metadata6.csv')
output_csv = Path('../../output/amazing_logos_v4/data/amazing_logos_v4_cleanup/categories_analysis4.json')
output_metadata_csv = Path('../../output/amazing_logos_v4/data/amazing_logos_v4_cleanup/metadata7.csv')

print(f"Input metadata CSV: {input_metadata_csv}")
print(f"Output categories JSON: {output_csv}")
print(f"Output metadata CSV: {output_metadata_csv}")

# Check if metadata input exists
if not input_metadata_csv.exists():
    print(f"ERROR: Input file {input_metadata_csv} does not exist!")
    print("Please run previous steps to create metadata3.csv.")
else:
    print(f"Input metadata file exists.")

Input metadata CSV: ..\output\amazing_logos_v4\data\amazing_logos_v4_metadata6.csv
Output categories JSON: ..\output\amazing_logos_v4\data\amazing_logos_v4_categories_analysis4.json
Output metadata CSV: ..\output\amazing_logos_v4\data\amazing_logos_v4_metadata7.csv
Input metadata file exists.


In [2]:
# Load metadata and create category analysis
print("Loading metadata and analyzing categories...")
df_metadata = pd.read_csv(input_metadata_csv)

print(f"Loaded metadata: {len(df_metadata):,} rows")
print(f"Columns: {list(df_metadata.columns)}")


# Find categories that are only digits
numeric_mask = df_metadata['category'].astype(str).str.match(r'^\d+$', na=False)
numeric_categories = df_metadata[numeric_mask]['category'].tolist()
numeric_count = numeric_mask.sum()

if numeric_count > 0:
    print(f"Found {numeric_count} numeric-only categories")

    
    # Replace numeric categories with NA
    df_metadata.loc[numeric_mask, 'category'] = pd.NA
    print(f"\nReplaced {numeric_count} numeric categories with NA")
    
    # set rows with NA categories for consolidation to 'na' string
    df_metadata.loc[df_metadata.category.isna(), 'category'] = 'na'
else:
    print("No numeric-only categories found")
df_for_consolidation = df_metadata.copy()

Loading metadata and analyzing categories...
Loaded metadata: 393,297 rows
Columns: ['id', 'company', 'description', 'category', 'tags']
No numeric-only categories found


In [3]:
print(df_for_consolidation.category.value_counts().index.tolist())

['unclassified', 'real_estate_residential', 'restaurant_dining', 'healthcare_general', 'nonprofit_charity', 'design_creative', 'sports_recreation', 'education_k12', 'fashion_apparel', 'food', 'medical_specialty', 'music_industry', 'retail_general', 'construction_general', 'entertainment_venues', 'marketing_advertising', 'financial_services', 'photography_video', 'arts_culture', 'travel_tourism', 'other_services', 'brewery_alcohol', 'religious_faith', 'printing_publishing', 'hospitality_services', 'web_digital', 'software_development', 'cafe_coffee', 'legal_services', 'it_services', 'catering_events', 'fitness_health', 'film_video', 'beauty_cosmetics', 'financial', 'home_improvement', 'agriculture_farming', 'automotive_transport', 'government_public', 'manufacturing_general', 'telecommunications', 'food_beverage', 'beverage_general', 'media_publishing', 'real_estate_development', 'home_goods', 'energy_utilities', 'food_and_beverage', 'dental_services', 'insurance_services', 'hotels_lodg

In [3]:
# Use consolidation function to get consolidated categories
print("\n=== CONSOLIDATING CATEGORIES ===")
print("Using consolidation.py utility...")

# Apply consolidation to cleaned data (excluding numeric categories)
df_consolidated, unmatched_categories, consolidation_mapping = consolidate_categories(df_for_consolidation)

print(f"\nConsolidation complete!")
print(f"Consolidated categories: {len(consolidation_mapping)}")
print(f"Unmatched categories: {len(unmatched_categories)}")
print(f"Total logos processed: {len(df_consolidated):,}")

# Show some statistics about the consolidation
total_logos = sum(data['count'] for data in consolidation_mapping.values())
print(f"Total logos in consolidation mapping: {total_logos:,}")

print(f"\n=== TOP 10 CONSOLIDATED CATEGORIES ===")
sorted_categories = sorted(consolidation_mapping.items(), key=lambda x: x[1]['count'], reverse=True)
for i, (category, data) in enumerate(sorted_categories[:10], 1):
    percentage = (data['count'] / total_logos) * 100 if total_logos > 0 else 0
    num_originals = len(data['original_categories'])
    print(f"{i:2d}. {category:<30} {data['count']:>7} ({percentage:>5.2f}%) [{num_originals:>3} orig]")


=== CONSOLIDATING CATEGORIES ===
Using consolidation.py utility...
DEBUG: Processing 'vacation_recreation' -> normalized: 'vacation recreation'
DEBUG: Exact match found: 'vacation recreation' -> 'hospitality_travel'
DEBUG: Processing 'brewery_alcohol' -> normalized: 'brewery alcohol'
DEBUG: Exact match found: 'brewery alcohol' -> 'food_beverage'
DEBUG: Processing 'real_estate_residential' -> normalized: 'real estate residential'
DEBUG: Exact match found: 'real estate residential' -> 'real_estate_property'
DEBUG: Processing 'radio_podcast' -> normalized: 'radio podcast'
DEBUG: Exact match found: 'radio podcast' -> 'media_communications'
DEBUG: Processing 'Photographers Services' -> normalized: 'photographers services'
DEBUG: No match found for 'photographers services', keeping original
DEBUG: Processing 'jewelry_accessories' -> normalized: 'jewelry accessories'
DEBUG: Exact match found: 'jewelry accessories' -> 'retail_consumer_goods'
DEBUG: Processing 'Automobile Parts' -> normalized:

In [4]:
df_consolidated.category.value_counts()

category
miscellaneous_other                31455
food_beverage                      22676
design_creative                    21450
healthcare_medical                 17976
government_public_services         16620
                                   ...  
Hair and Skincare                      1
Music. Artist Management               1
Fitness Yoga                           1
Food Healthy Snacks                    1
Plants Landscaping Conservation        1
Name: count, Length: 46299, dtype: int64

In [5]:
# Create the final DataFrame with required format
print("\n=== CREATING FINAL OUTPUT ===")

final_data = []
for category, data in consolidation_mapping.items():
    # Join original categories with commas
    original_categories_str = ', '.join(sorted(set(data['original_categories'])))
    
    final_data.append({
        'category': category,
        'count': data['count'],
        'original_categories': original_categories_str
    })

# Create DataFrame and sort by count
df_final = pd.DataFrame(final_data)
df_final = df_final.sort_values('count', ascending=False).reset_index(drop=True)

print(f"Created final DataFrame with {len(df_final)} consolidated categories")
print(f"Total logos: {df_final['count'].sum():,}")

# Show top consolidated categories
print(f"\n=== TOP 20 CONSOLIDATED CATEGORIES ===")
for i, row in df_final.head(20).iterrows():
    percentage = (row['count'] / df_final['count'].sum()) * 100
    num_originals = len(row['original_categories'].split(', '))
    print(f"{i+1:2d}. {row['category']:<30} {row['count']:>7} ({percentage:>5.2f}%) [{num_originals:>3} orig]")


=== CREATING FINAL OUTPUT ===
Created final DataFrame with 46299 consolidated categories
Total logos: 393,297

=== TOP 20 CONSOLIDATED CATEGORIES ===
 1. miscellaneous_other              31455 ( 8.00%) [ 49 orig]
 2. food_beverage                    22676 ( 5.77%) [ 42 orig]
 3. design_creative                  21450 ( 5.45%) [123 orig]
 4. healthcare_medical               17976 ( 4.57%) [ 25 orig]
 5. government_public_services       16620 ( 4.23%) [ 60 orig]
 6. sports_recreation                14957 ( 3.80%) [ 37 orig]
 7. technology_software              13819 ( 3.51%) [126 orig]
 8. real_estate_property             13403 ( 3.41%) [ 32 orig]
 9. arts_culture_entertainment       12137 ( 3.09%) [ 16 orig]
10. media_communications             11967 ( 3.04%) [ 77 orig]
11. hospitality_travel               10455 ( 2.66%) [ 71 orig]
12. construction_home_services       10422 ( 2.65%) [ 53 orig]
13. education_training               10242 ( 2.60%) [ 52 orig]
14. textiles_clothing         

In [6]:
# Save the consolidated analysis
print(f"\nSaving consolidated analysis to {output_csv}...")

# Create category analysis from consolidation mapping
original_categories_count = len(set(cat for data in consolidation_mapping.values() for cat in data['original_categories']))

# Create JSON-friendly output with explicit type conversion to avoid int64 serialization issues
output_data = {
    "metadata": {
        "original_categories_count": int(original_categories_count),
        "numeric_categories_removed": int(numeric_count if 'numeric_count' in locals() else 0),
        "categories_after_cleaning": int(len(df_for_consolidation)),
        "final_consolidated_categories": int(len(df_final)),
        "total_reduction_factor": float(round(original_categories_count / len(df_final), 1)),
        "total_logos": int(df_final['count'].sum()),
        "consolidation_timestamp": pd.Timestamp.now().isoformat()
    },
    "consolidated_categories": []
}

# Add consolidated categories data with explicit type conversion
for _, row in df_final.iterrows():
    output_data["consolidated_categories"].append({
        "category": str(row['category']),
        "count": int(row['count']),
        "percentage": float(round((row['count'] / df_final['count'].sum()) * 100, 2)),
        "original_categories": [str(cat.strip()) for cat in row['original_categories'].split(', ')]
    })

# Save as JSON
import json
with open(output_csv, 'w', encoding='utf-8') as f:
    json.dump(output_data, f, indent=2, ensure_ascii=False)

print(f"Consolidated analysis saved successfully as JSON!")

# Show final statistics
print(f"\n=== FINAL STATISTICS ===")
print(f"Original categories (before cleaning): {original_categories_count:,}")
print(f"Numeric categories removed: {numeric_count if 'numeric_count' in locals() else 0}")
print(f"Categories after cleaning: {len(df_for_consolidation):,}")
print(f"Final consolidated categories: {len(df_final)}")
print(f"Total reduction factor: {original_categories_count / len(df_final):.1f}x")
print(f"Total logos: {df_final['count'].sum():,}")
print(f"Output file: {output_csv}")
print(f"Columns: {list(df_final.columns)}")

# Show some examples of the mapping
print(f"\n=== SAMPLE MAPPING EXAMPLES ===")
for i, row in df_final.head(5).iterrows():
    original_list = row['original_categories'].split(', ')[:5]  # Show first 5 original categories
    print(f"\n{row['category']} ({row['count']} logos):")
    for orig in original_list:
        print(f"  - {orig}")
    if len(row['original_categories'].split(', ')) > 5:
        remaining = len(row['original_categories'].split(', ')) - 5
        print(f"  ... and {remaining} more")


Saving consolidated analysis to ..\output\amazing_logos_v4\data\amazing_logos_v4_categories_analysis4.json...
Consolidated analysis saved successfully as JSON!

=== FINAL STATISTICS ===
Original categories (before cleaning): 47,929
Numeric categories removed: 0
Categories after cleaning: 393,297
Final consolidated categories: 46299
Total reduction factor: 1.0x
Total logos: 393,297
Output file: ..\output\amazing_logos_v4\data\amazing_logos_v4_categories_analysis4.json
Columns: ['category', 'count', 'original_categories']

=== SAMPLE MAPPING EXAMPLES ===

miscellaneous_other (31455 logos):
  - Advisors
  - Advisory
  - Artisan
  - Broker
  - Brokers
  ... and 44 more

food_beverage (22676 logos):
  - Brewery Alcohol Drinks
  - Brewery Drinks Alcohol
  - Catering & Events
  - Catering and Events
  - Catering and events
  ... and 37 more

design_creative (21450 logos):
  - Annual Exhibition Design
  - Architectural Lighting Design
  - Architecture Landscape
  - Art & Design Exhibition
  -

In [7]:
# Apply consolidation to metadata3.csv to create metadata4.csv
print(f"\n=== APPLYING CONSOLIDATION TO METADATA ===")
print(f"Using metadata already loaded from {input_metadata_csv}...")

print(f"Metadata: {len(df_metadata):,} rows")
print(f"Columns: {list(df_metadata.columns)}")

# Create mapping dictionary from original to consolidated categories
category_mapping = {}
for _, row in df_final.iterrows():
    consolidated_cat = row['category']
    original_cats = row['original_categories'].split(', ')
    for orig_cat in original_cats:
        category_mapping[orig_cat.strip()] = consolidated_cat

# Also handle numeric categories
if 'numeric_categories' in [row['category'] for _, row in df_final.iterrows()]:
    for num_cat in numeric_categories:
        category_mapping[str(num_cat)] = 'numeric_categories'

print(f"Created mapping for {len(category_mapping)} original categories")

# Apply consolidation to metadata
df_metadata_consolidated = df_metadata.copy()

# Track consolidation statistics
original_categories_in_metadata = df_metadata_consolidated['category'].value_counts()
consolidation_stats = {'mapped': 0, 'unmapped': 0, 'na_values': 0}

def consolidate_category(category):
    """Apply consolidation mapping to a single category"""
    if pd.isna(category):
        consolidation_stats['na_values'] += 1
        return pd.NA
    
    category_str = str(category).strip()
    if category_str in category_mapping:
        consolidation_stats['mapped'] += 1
        return category_mapping[category_str]
    else:
        consolidation_stats['unmapped'] += 1
        return 'unclassified'

# Apply consolidation
print("Applying category consolidation to metadata...")
df_metadata_consolidated['category'] = df_metadata_consolidated['category'].apply(consolidate_category)

print(f"\n=== CONSOLIDATION STATISTICS ===")
print(f"Categories mapped to consolidated: {consolidation_stats['mapped']:,}")
print(f"Categories mapped to 'unclassified': {consolidation_stats['unmapped']:,}")
print(f"NA values preserved: {consolidation_stats['na_values']:,}")
print(f"Total rows processed: {len(df_metadata_consolidated):,}")

# Show before/after category distribution
print(f"\n=== CATEGORY DISTRIBUTION COMPARISON ===")
print(f"Original unique categories: {df_metadata['category'].nunique()}")
print(f"Consolidated unique categories: {df_metadata_consolidated['category'].nunique()}")

print(f"\nTop 10 consolidated categories in metadata:")
consolidated_counts = df_metadata_consolidated['category'].value_counts().head(10)
for i, (cat, count) in enumerate(consolidated_counts.items(), 1):
    percentage = (count / len(df_metadata_consolidated)) * 100
    print(f"{i:2d}. {cat:<25} {count:>7} ({percentage:>5.2f}%)")

# Save consolidated metadata
print(f"\nSaving consolidated metadata to {output_metadata_csv}...")
df_metadata_consolidated.to_csv(output_metadata_csv, index=False)
print(f"Consolidated metadata saved successfully!")

print(f"\n=== FINAL OUTPUT FILES ===")
print(f"Categories analysis (JSON): {output_csv}")
print(f"Consolidated metadata (CSV): {output_metadata_csv}")
print(f"Total logos with consolidated categories: {len(df_metadata_consolidated):,}")


=== APPLYING CONSOLIDATION TO METADATA ===
Using metadata already loaded from ..\output\amazing_logos_v4\data\amazing_logos_v4_metadata4.csv...
Metadata: 393,297 rows
Columns: ['id', 'company', 'description', 'category', 'tags']
Created mapping for 47929 original categories
Applying category consolidation to metadata...

=== CONSOLIDATION STATISTICS ===
Categories mapped to consolidated: 393,297
Categories mapped to 'unclassified': 0
NA values preserved: 0
Total rows processed: 393,297

=== CATEGORY DISTRIBUTION COMPARISON ===
Original unique categories: 47929
Consolidated unique categories: 46299

Top 10 consolidated categories in metadata:
 1. miscellaneous_other         31455 ( 8.00%)
 2. food_beverage               22676 ( 5.77%)
 3. design_creative             21450 ( 5.45%)
 4. healthcare_medical          17976 ( 4.57%)
 5. government_public_services   16620 ( 4.23%)
 6. sports_recreation           14957 ( 3.80%)
 7. technology_software         13819 ( 3.51%)
 8. real_estate_pro